# Kiihtyvyysmittauksia CMS-koeaseman hississä

Tämä harjoite on esimerkki helposti tehtävästä mittaustyöstä analyyseineen. Alkuperäinen työ toteutettiin vuoden 2024 CERNin opettajakurssille osallistuneitten toimesta.

### 1. Työkalupaketit

In [ ]:
# Ladataan kirjastot
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
from scipy.stats import norm
from scipy import integrate

### 2. Aineisto

Avataan .csv-tiedosto, joka sisältää puhelimen Phyphox-ohjelmalla [https://phyphox.org/](https://phyphox.org/) mitattua sensoridataa. Tarkastellaan miltä se näyttää. Data pitää sisällään puhelimen kiihtyvyysanturin mittaukset ajan suhteen, kun CMS-koeaseman hissillä tullaan alhaalta ylös.

In [ ]:
df = pd.read_csv('https://raw.githubusercontent.com/opendata-education/Tyopajat/refs/heads/main/materiaali/data/CMS-hissi.csv', delimiter = ";")
df.head()

In [ ]:
# Acceleration z (m/s^2) on kiihtyvyys puhelimen näyttöön kohtisuorassa suunnassa, eli suunta josta olemme kiinnostuneita.
# Time (s) on kulunut aika.
# Poistetaan ylimääräinen data pudottamalla turhat sarakkeet muuttujasta df.

df.drop(columns = ['Acceleration x (m/s^2)', 'Acceleration y (m/s^2)',"Absolute acceleration (m/s^2)"], inplace = True)

### 3. Analyysi

In [ ]:
# Tarkastellaan datasta alkuun, miltä kiihtyvyys näyttää ajan funktiona.

fig = plt.figure(figsize = (10,3))
plt.plot(df['Time (s)'], df['Acceleration z (m/s^2)'])

plt.xlabel(r'$t\;(\text{s})$')
plt.ylabel(r'$a\;(\text{m/s}^2$)')
plt.title('CMS-hissin kiihtyvyys')
plt.show()

Datasta voidaan päätellä, että puhelin on aluksi ollut näyttö kohden taivasta, minkä jälkeen puhelin on käännetty ylösalaisin ja asetettu hissin lattialle.

In [ ]:
# Valitaan datasta tämän takia tarkasteluun väli aikaväli 20-85 s, jolloin
# puhelin on alussa vielä paikoillaan, näyttö kohden hissin lattiaa ja hissi on
# vielä paikoillaan.

df = df.loc[(df['Time (s)'] >= 20) & (df['Time (s)'] <= 85)]

In [ ]:
# Tarkastellaan dataa valitulla välillä.

fig = plt.figure(figsize=(10,3))
plt.plot(df['Time (s)'], df['Acceleration z (m/s^2)'])

plt.xlabel(r'$t\;(\text{s})$')
plt.ylabel(r'$a\;(\text{m/s}^2$)')
plt.title('CMS-hissin kiihtyvyys')

plt.show()

Huomataan, että anturi ilmoittaa kiihtyvyydeksi paikallaan ollessaan noin -9,8 $m/s^2$. Poistetaan tämä esityksestämme määrittämällä keskiarvo kiihtyvyydestä välillä 20-29 s, kun hissi on paikallaan ennen liikkeelle lähtöä. 

In [ ]:
# Lasketaan keskiarvo tuolta ajalta ja poistetaan se datasta.
# lisäksi käännetään samalla sensorin suunta ottamalla vastaluvut.

a_err = df.loc[df['Time (s)'] <= 29, 'Acceleration z (m/s^2)'].mean()
df.insert(len(df.columns),'Acceleration (m/s^2)',df.loc[:,'Acceleration z (m/s^2)']*(-1)+a_err)
df.head()

In [ ]:
# Tarkastellaan dataa korjatulla kiihtyvyyden arvolla.

fig = plt.figure(figsize=(10,3))
plt.plot(df['Time (s)'], df['Acceleration (m/s^2)'])

plt.xlabel(r'$t\;(\text{s})$')
plt.ylabel(r'$a\;(\text{m/s}^2$)')
plt.title('CMS-hissin kiihtyvyys')

plt.show()

In [ ]:
# Määritetään nopeus integroimalla numeerisesti kiihtyvyysdataa ajan suhteen.

velocities = integrate.cumulative_trapezoid(df['Acceleration (m/s^2)'], x=df['Time (s)'], axis=0, initial=0)
df.insert(len(df.columns),'Velocity (m/s)', velocities)

# Määritetään korkeus integroimalla numeerisesti nopeus ajan suhteen.

elevation = integrate.cumulative_trapezoid(df['Velocity (m/s)'], x=df['Time (s)'], axis=0, initial=0)
df.insert(len(df.columns),'Elevation (m)', elevation)

df.head()

In [ ]:
# Piirretään kuvaaja hissin liikkeestä.

fig, (ax1, ax2, ax3) = plt.subplots(3, sharex=True)
fig = plt.figure(figsize=(10,9))

ax1.set_title('CMS-hissin liike')

ax1.plot(df['Time (s)'], df['Acceleration (m/s^2)'])
ax2.plot(df['Time (s)'], df['Velocity (m/s)'])
ax3.plot(df['Time (s)'], df['Elevation (m)'])

ax1.set_ylabel('$a$ (m/s$^2$)')
ax2.set_ylabel('$v$ (m/s)')
ax3.set_ylabel('$h$ (m)')
ax3.set_xlabel('$t$ (s)')

plt.show()

In [ ]:
# Muutos korkeudessa, joka hissillä noustessa tehtiin.

print(df["Elevation (m)"].max(),"metriä")

### 4. Johtopäätökset

Tavallisella kännykällä saatiin aika uskottavasti näkyviin kuinka tyypillinen hissi saadaan liikkeelle ja uudelleen lepoon määränpäässään. Voidaanko liikkeen sanoa olleen tasaista vai kiihtyvää matkan aikana?